# 基于搜索的自动量化概述

参考：[RFC: 5483](https://discuss.tvm.apache.org/t/rfc-search-based-automated-quantization/5483)

量化流程：![](images/ap-intro.png)

- 注解（Annotation）：注解过程重写计算图，并根据每个算子的重写函数插入模拟量化算子。模拟量化算子模拟了从浮点数到整数量化的舍入误差（rounding error）和饱和误差（saturating error）。
- 校准（Calibration）：校准过程将调整模拟量化算子的阈值以减少精度下降。
- 实现（Realization）：实现过程将模拟计算图（实际上用 `float32` 计算）转换为真正的低精度整数计算图。

In [2]:
%cd ..
import set_env

/media/pc/data/lxw/ai/tvm-book/doc/tutorials


In [3]:
from tvm.relay.quantize._annotate import simulated_quantize_compute

模拟量化计算如下：

In [4]:
simulated_quantize_compute??

Signature: simulated_quantize_compute(attrs, inputs, out_type)
Source:   
@_op.register_compute("relay.op.annotation.simulated_quantize")
def simulated_quantize_compute(attrs, inputs, out_type):
    """Compiler for simulated_quantize."""
    assert len(inputs) == 4
    assert attrs.sign
    assert attrs.rounding == "round"

    data, scale, clip_min, clip_max = inputs

    if attrs.kind == QAnnotateKind.IDENTITY:
        return [topi.identity(data)]

    # simulate rounding error
    scaled_data = topi.divide(data, scale)
    clipped_data = topi.maximum(topi.minimum(scaled_data, clip_max), clip_min)
    round_data = topi.round(clipped_data)

    # recover data
    rdata = topi.multiply(round_data, scale)
    return [rdata]
File:      /media/pc/data/lxw/ai/tvm/python/tvm/relay/quantize/_annotate.py
Type:      function